In [42]:
import pandas as pd
import yfinance as yf
import datetime as dt
import matplotlib.pyplot as plt
import mplfinance as mpl
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.graph_objects as go
'''
戦略
ボラティリティー低下でシグナルを出す
上放れした時点で買い
ストップは順次あげていく
'''

#install symbols nasdaq100の銘柄コード
# df = pd.read_csv('../symbols/nasdaq100.csv')

# sign = []
# for symbol in df['symbol']:
#     sign.append(symbol)
    

sign = ['6976.T','4477.T','6036.T']
    

totalresult = []

for i in sign:
    stock_code = i 
    start = '2019-01-01'
    end = '2021-02-02'
    df = yf.download(stock_code, start, end, interval='1d') 
    
    
    print(i)
    term=81
    # chek the highest price in the past {term} times
    df['Highest'+str(term)] = df.iloc[:, 4].rolling(window=term).max()
    print(df.head())
    
        
    
    # calculation SMA
    short_sma = 25
    long_sma = 50
    verylong_sma = 250
    #'term'日間の移動平均線
    df['SMA'+str(short_sma)] = df['Adj Close'].rolling(window=short_sma).mean()
    df['SMA'+str(long_sma)] = df['Adj Close'].rolling(window=long_sma).mean()
    df['SMA'+str(verylong_sma)] = df['Adj Close'].rolling(window=verylong_sma).mean()
      
    #slope of the sma
    def diff(x):
        return x[-1] - x[0]
    trend_term = 2
    df['SMA Trend'] = df['SMA'+str(short_sma)].rolling(window=trend_term).apply(diff)
    
     # 損切り率
    stopLoss = 0.94
    
    # signal 判断
    signal_arart = 0
 
    
    #買い日と売り日
    buy_days = []
    sell_days = []
    signal_days = []
    
    #holding period list
    holding_period_list = []


    #calucurate Bband
    df['MA'] = df['Adj Close'].rolling(window=20).mean()
    df['STD'] = df['Adj Close'].rolling(window=20).std()
    df['Upper'] = df['MA'] + (df['STD'] * 2)
    df['Lower'] = df['MA'] - (df['STD'] * 2)
    
    #daviation_rate
    df['daviation_rate'] = 100 * (df['Adj Close'] - df['SMA'+str(short_sma)]) / df['SMA'+str(short_sma)]

    #Standard deviation normalization
    df['Standard_deviation_normalization'] = 100 * 2 * df['STD'] / df['SMA'+str(short_sma)]
   
    buy_position = False
    percentChange = []
    for i in range(1, len(df)):
        close = df['Adj Close'][i]
        STD = df['STD'][i]
        high_price = df['High'][i]
        low_price = df['Low'][i]
        open_price = df['Open'][i]
        sma = df['SMA'+str(short_sma)][i]
        SDN = df['Standard_deviation_normalization'][i]
        daviation_rate = df['daviation_rate'][i]
        Highest = df['Highest'+str(term)][i-1]
        

    
        if np.isnan(df['MA'][i]) == False:
            if buy_position == False and SDN < 10 and -5 < daviation_rate < 5 :
#                 print('low volatility')
                signalday = pd.to_datetime(df.index[i])
                signal_days.append(i)
                print(signalday)
                signal_arart = 1
        
        if signal_arart == 1 and(pd.to_datetime(i) - signalday).days < 7 and close > Highest and buy_position == False:
            buy_position = True
            buyday = pd.to_datetime(df.index[i])
            buy_days.append(buyday)
            buy_price = close
            buy_stopLine = close * stopLoss
            buypoint = i
            current_stop_level = 0
            print('buy in {} at {}'.format(buyday,buy_price))
            signal_arart = 0
           
        
        #adjustment stopline
        if buy_position == True and close > buy_price * 1.05 and current_stop_level == 0:
            buy_stopLine = buy_price
            current_stop_level = 1
            print('up stopline1 in {} at {}'.format(df.index[i],buy_stopLine))
            
        if buy_position == True and close > buy_price * 1.1 and current_stop_level == 1:
            buy_stopLine = buy_price * 1.05
            current_stop_level = 2
            print('up stopline2 in {} at {}'.format(df.index[i],buy_stopLine))
           
            
        if buy_position == True and close > buy_price * 1.2 and current_stop_level == 2:
            buy_stopLine = buy_price * 1.1
            current_stop_level = 3
            print('up stopline3 in {} at {}'.format(df.index[i],buy_stopLine))
            
        if buy_position == True and close > buy_price * 1.3 and current_stop_level == 3:
            buy_stopLine = close * 0.85
            current_stop_level = 4
            print('up stopline4 in {} at {}'.format(df.index[i],buy_stopLine))
            
        if buy_position == True and close > buy_price * 1.5 and current_stop_level == 4:
            buy_stopLine = close * 0.8
            current_stop_level = 5  
            print('up stopline5 in {} at {}'.format(df.index[i],buy_stopLine))
            
            
        if buy_position == True and close > Highest and current_stop_level == 5:
            buy_stopLine = close * 0.8
            current_stop_level = 5  
            print('up stopline6 in {} at {}'.format(df.index[i],buy_stopLine))
            
            
            
         # 損切り or Profit taking
        if buy_position == True and open_price < buy_stopLine and i != buypoint:
            buy_position = False 
            percent = (open_price/buy_price - 1) * 100
            percentChange.append(percent)
            sellday = pd.to_datetime(df.index[i])
            sell_days.append(sellday)
            holding_period = sellday - buyday
            print('sell in {} at {} | profit_one is {}'.format(sellday,open_price,percent))
            
        elif buy_position == True and close < buy_stopLine and i != buypoint:
            buy_position = False 
            percent = (buy_stopLine/buy_price - 1) * 100
            percentChange.append(percent)
            sellday = pd.to_datetime(df.index[i])
            sell_days.append(sellday)
            holding_period = sellday - buyday
            holding_period_list.append(holding_period.days)
            print('sell in {} at {} | profit_two is {}'.format(sellday,buy_stopLine,percent))

        #  最終日にまだ持ってたら利確する
        if i == (len(df)-1) and buy_position == True:
            buy_position = False
            percent = (close / buy_price - 1) * 100
            percentChange.append(percent)
            sellday = pd.to_datetime(df.index[i])
            sell_days.append(sellday)
            holding_period = sellday - buyday
            holding_period_list.append(holding_period.days)
            print('Date:'+str(i),'Last Day Buy at the price {}'.format(close))

       
    # statistic
#     ------------------------------------------
    gains = 0
    losses = 0
    numlosses = 0
    numgains = 0
    total_return = 1


    for i in percentChange:
        if i > 0:
            numgains += 1
            gains += i
        else:
            numlosses += 1
            losses += i
        total_return = total_return * ((i / 100) + 1)
        
        
    total_return = round((total_return - 1)*100, 2)
    if numgains > 0:
        ave_gain = gains / numgains
#         max_return = max(percentChange)
    else:
        ave_gain = 0
        max_return = 'unknown'
    
    if numlosses > 0:
        ave_loss = losses / numlosses
#         max_loss = min(percentChange)
        risk_reward_retio = - ave_gain / ave_loss
    else:
        ave_loss = 0
        max_loss = 'unknown'
        risk_reward_retio = 'inf'
    
    if numgains > 0 or numlosses > 0:
        batting_retio = numgains / (numgains + numlosses)
    else:
        batting_retio = 0
    
    trades = numgains + numlosses
    ave_total = ave_gain * batting_retio + ave_loss * (1 - batting_retio)
    
    #average holding period
    if len(holding_period_list) != 0:   
        average_holding_period = sum(holding_period_list)/len(holding_period_list)
    

    results = [numgains+numlosses, round(total_return,2), round(ave_gain,2), round(ave_loss,2)
               ,batting_retio ,ave_total ,average_holding_period]
    
    if not results is None:
         totalresult.append(results)
            


    #plot figure --------------------------------------------------------- 
#     Add shapes
    signal_signals = []
    for i in df.index:
        if i in signal_days:
            signal_signals.append(df['Adj Close'][i])
        else:
            signal_signals.append(np.nan)
    signal_df = pd.DataFrame({'signal_signals':signal_signals})

    
    x = np.arange(len(df.index)) #x軸を0からデータの個数まで1ずつ増える数列
    labels = df.index #x軸ラベルを日付にする

    
    trace0 = go.Candlestick(x = df.index, open=df['Open'],high=df['High'],low=df['Low'],close=df['Close'],
                         xaxis='x1', yaxis = 'y1', name  = stock_code)
    trace1 = go.Scatter(x = df.index, y = df['SMA'+str(short_sma)], mode = 'lines',xaxis='x1',yaxis = 'y1')
    trace2 = go.Scatter(x = df.index, y = df['SMA'+str(long_sma)], mode = 'lines',xaxis='x1',yaxis = 'y1')
    trace3 = go.Scatter(x = df.index, y = df['SMA'+str(verylong_sma)], mode = 'lines',xaxis='x1',yaxis = 'y1')
    trace4 = go.Scatter(x = df.index, y = df['Upper'], mode = 'lines',xaxis='x1',yaxis = 'y1')
    trace5 = go.Scatter(x = df.index, y = df['Lower'], mode = 'lines',xaxis='x1',yaxis = 'y1')
    trace6 = go.Scatter(x = df.index, y = df['Standard_deviation_normalization'], 
                                                  mode = 'lines',xaxis='x2',yaxis = 'y2')
    trace7 = go.Scatter(x = df.index, y = df['daviation_rate'], mode = 'lines',xaxis='x3',yaxis = 'y3')
    trace8 = go.Scatter(x = df.index, y = signal_df ,yaxis = 'y1')
     
        
    data = [trace0, trace1, trace2, trace3, trace6, trace7]
        
    
    # レイアウトの指定
#     layout = go.Layout(xaxis = dict(domain=[0, 0.45]), yaxis=dict(domain=[0, 0.45]),
#                        xaxis2 = dict(domain=[0, 0.45]), yaxis2 = dict(domain=[0, 0.45]) ,
#                        xaxis3 = dict(domain=[0, 0.45]), yaxis3 = dict(domain=[0, 0.45]) )
    
#     fig = go.Figure(data=data, layout=layout)
#     fig.show()
    
    
    
    fig = make_subplots(rows=3, cols=1
                              )
    
    fig.append_trace(trace0, 1, 1)
    fig.append_trace(trace1, 1, 1)
    fig.append_trace(trace2, 1, 1)
    fig.append_trace(trace3, 1, 1)
    fig.append_trace(trace8, 1, 1)
    fig.append_trace(trace6, 2, 1)
    fig.append_trace(trace7, 3, 1)
    
    
    

    fig.update_layout(height=1000, width=1000, title_text="Stacked Subplots")
    fig.show()
    

   
        
        
    
    
   
                
                
    
    
#     make figure
#     df['70'] = 70
#     df['30'] = 30
#     df['50'] = 50
#     df['0'] = 0
    
#     signal_signals = []
#     for i in df.index:
#         if i in signal_days:
#             signal_signals.append(df['Adj Close'][i])
#         else:
#             signal_signals.append(np.nan)
            
            
#     if np.all(signal_signals) == True:
#         apds = [
#         mpl.make_addplot( df['Volume'] , panel=3, ylabel='Volume'),
#         mpl.make_addplot(df['Upper'], type='line' ,color="r"),
#         mpl.make_addplot(df['Lower'], type='line',color="r"),
#         mpl.make_addplot(df['Standard_deviation_normalization'], panel=1, type='line', ylabel='STD'),
#         mpl.make_addplot( df[['daviation_rate','0']] , panel=2, type='line', ylabel='daviation_rate'),
#         mpl.make_addplot(signal_signals, type='scatter', markersize=10000, marker='|', color="b"),
#         ]
   

#         fig = mpl.plot(df, type='candle',figsize=(30, 15), style='yahoo',mav=(short_sma, long_sma, verylong_sma)
#                        , addplot=apds, title=str(stock_code))



# columns = ['trades', 'Total return', 'Average Gain', 'Average Loss', '勝率' ,'Average gain and profit','average holding period']
# df = pd.DataFrame(totalresult, columns=columns, index = sign)
# df.to_csv('./volatility_result.csv')

print(df)
        

[*********************100%***********************]  1 of 1 completed
ATVI
                 Open       High        Low      Close  Adj Close   Volume  \
Date                                                                         
2018-12-31  47.040001  47.320000  46.009998  46.570000  45.897026  7789600   
2019-01-02  45.250000  47.509998  45.139999  47.029999  46.350380  7245700   
2019-01-03  46.439999  46.650002  45.000000  45.360001  44.704514  8266400   
2019-01-04  46.000000  47.549999  45.130001  47.169998  46.488358  9081900   
2019-01-07  47.240002  49.080002  47.090000  48.500000  47.799141  9112100   

            Highest81  
Date                   
2018-12-31        NaN  
2019-01-02        NaN  
2019-01-03        NaN  
2019-01-04        NaN  
2019-01-07        NaN  
2019-02-05 00:00:00
2019-02-13 00:00:00
2019-02-14 00:00:00
2019-02-15 00:00:00
2019-02-19 00:00:00
2019-02-28 00:00:00
2019-03-01 00:00:00
2019-03-04 00:00:00
2019-03-05 00:00:00
2019-03-06 00:00:00
2019-03-07 

[*********************100%***********************]  1 of 1 completed
ADBE
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-12-31  225.559998  227.330002  223.240005  226.240005  226.240005   
2019-01-02  219.910004  226.169998  219.000000  224.570007  224.570007   
2019-01-03  220.880005  223.630005  215.149994  215.699997  215.699997   
2019-01-04  219.839996  227.649994  217.479996  226.190002  226.190002   
2019-01-07  229.949997  232.600006  227.289993  229.259995  229.259995   

             Volume  Highest81  
Date                            
2018-12-31  2866400        NaN  
2019-01-02  2784100        NaN  
2019-01-03  3663500        NaN  
2019-01-04  4043400        NaN  
2019-01-07  3638500        NaN  
2019-02-14 00:00:00
2019-02-15 00:00:00
2019-02-19 00:00:00
2019-02-20 00:00:00
2019-02-21 00:00:00
2019-02-22 00:00:00
2019-02-25 00:00:00
2019-02-26 00:00:00
2019-02-27 00:00

[*********************100%***********************]  1 of 1 completed
AMD
                 Open   High        Low      Close  Adj Close     Volume  \
Date                                                                       
2018-12-31  18.150000  18.51  17.850000  18.459999  18.459999   84732200   
2019-01-02  18.010000  19.00  17.980000  18.830000  18.830000   87148700   
2019-01-03  18.420000  18.68  16.940001  17.049999  17.049999  117277600   
2019-01-04  17.549999  19.07  17.430000  19.000000  19.000000  111878600   
2019-01-07  19.440001  20.68  19.000000  20.570000  20.570000  107157000   

            Highest81  
Date                   
2018-12-31        NaN  
2019-01-02        NaN  
2019-01-03        NaN  
2019-01-04        NaN  
2019-01-07        NaN  
2019-02-27 00:00:00
2019-02-28 00:00:00
2019-03-01 00:00:00
2019-03-04 00:00:00
2019-03-05 00:00:00
2019-03-06 00:00:00
2019-03-11 00:00:00
2019-03-12 00:00:00
2019-03-13 00:00:00
2019-03-14 00:00:00
2019-03-15 00:00:00
2019-0

[*********************100%***********************]  1 of 1 completed
ALXN
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-12-31   98.059998   99.809998   96.389999   97.360001   97.360001   
2019-01-02   95.839996   99.050003   95.160004   98.050003   98.050003   
2019-01-03  100.150002  103.879997   99.120003  100.209999  100.209999   
2019-01-04  101.879997  107.300003  101.800003  106.000000  106.000000   
2019-01-07  105.650002  108.980003  104.699997  107.940002  107.940002   

             Volume  Highest81  
Date                            
2018-12-31  1310400        NaN  
2019-01-02  1359500        NaN  
2019-01-03  3296500        NaN  
2019-01-04  2349900        NaN  
2019-01-07  1983700        NaN  
2019-02-07 00:00:00
2019-02-08 00:00:00
2019-02-11 00:00:00
2019-02-21 00:00:00
2019-03-06 00:00:00
2019-03-07 00:00:00
2019-03-08 00:00:00
2019-03-11 00:00:00
2019-03-12 00:00

[*********************100%***********************]  1 of 1 completed
ALGN
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-12-31  209.889999  214.179993  206.679993  209.429993  209.429993   
2019-01-02  205.320007  207.160004  200.539993  202.119995  202.119995   
2019-01-03  200.029999  200.770004  183.619995  184.779999  184.779999   
2019-01-04  181.679993  190.389999  177.929993  186.710007  186.710007   
2019-01-07  187.410004  190.770004  184.509995  189.919998  189.919998   

             Volume  Highest81  
Date                            
2018-12-31   809300        NaN  
2019-01-02  1126800        NaN  
2019-01-03  2414200        NaN  
2019-01-04  2518200        NaN  
2019-01-07  1311200        NaN  
2019-03-04 00:00:00
2019-03-05 00:00:00
2019-03-11 00:00:00
2019-03-12 00:00:00
2019-03-13 00:00:00
2019-03-14 00:00:00
2019-03-15 00:00:00
2019-03-18 00:00:00
2019-03-19 00:00

...

[*********************100%***********************]  1 of 1 completed
AMZN
                   Open         High          Low        Close    Adj Close  \
Date                                                                          
2018-12-31  1510.800049  1520.760010  1487.000000  1501.969971  1501.969971   
2019-01-02  1465.199951  1553.359985  1460.930054  1539.130005  1539.130005   
2019-01-03  1520.010010  1538.000000  1497.109985  1500.280029  1500.280029   
2019-01-04  1530.000000  1594.000000  1518.310059  1575.390015  1575.390015   
2019-01-07  1602.310059  1634.560059  1589.189941  1629.510010  1629.510010   

             Volume  Highest81  
Date                            
2018-12-31  6954500        NaN  
2019-01-02  7983100        NaN  
2019-01-03  6975600        NaN  
2019-01-04  9182600        NaN  
2019-01-07  7993200        NaN  
2019-02-05 00:00:00
2019-02-06 00:00:00
2019-02-07 00:00:00
2019-02-08 00:00:00
2019-02-11 00:00:00
2019-02-12 00:00:00
2019-02-13 00:00:00
2

[*********************100%***********************]  1 of 1 completed
AEP
                 Open       High        Low      Close  Adj Close   Volume  \
Date                                                                         
2018-12-31  74.779999  75.089996  73.910004  74.739998  69.475731  2203300   
2019-01-02  74.610001  74.610001  72.470001  72.940002  67.802513  2679600   
2019-01-03  72.940002  73.660004  72.300003  72.769997  67.644478  3063500   
2019-01-04  72.320000  73.440002  72.260002  73.440002  68.267288  2857500   
2019-01-07  72.940002  73.209999  72.440002  73.029999  67.886169  3218400   

            Highest81  
Date                   
2018-12-31        NaN  
2019-01-02        NaN  
2019-01-03        NaN  
2019-01-04        NaN  
2019-01-07        NaN  
2019-02-05 00:00:00
2019-02-06 00:00:00
2019-02-12 00:00:00
2019-02-13 00:00:00
2019-02-14 00:00:00
2019-02-15 00:00:00
2019-02-19 00:00:00
2019-02-20 00:00:00
2019-02-21 00:00:00
2019-02-22 00:00:00
2019-02-25 0

[*********************100%***********************]  1 of 1 completed
AMGN
                  Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-12-31  191.929993  195.800003  191.610001  194.669998  182.486313   
2019-01-02  192.520004  193.199997  188.949997  191.899994  179.889648   
2019-01-03  192.149994  194.179993  188.669998  188.979996  177.152435   
2019-01-04  191.460007  196.520004  190.839996  195.440002  183.208115   
2019-01-07  194.759995  199.360001  194.000000  198.070007  185.673523   

             Volume  Highest81  
Date                            
2018-12-31  2764800        NaN  
2019-01-02  3009100        NaN  
2019-01-03  3973900        NaN  
2019-01-04  4193400        NaN  
2019-01-07  3032500        NaN  
2019-02-05 00:00:00
2019-02-06 00:00:00
2019-02-08 00:00:00
2019-02-11 00:00:00
2019-02-12 00:00:00
2019-02-13 00:00:00
2019-02-14 00:00:00
2019-02-15 00:00:00
2019-02-19 00:00

[*********************100%***********************]  1 of 1 completed
ADI
                 Open       High        Low      Close  Adj Close   Volume  \
Date                                                                         
2018-12-31  86.089996  86.540001  84.970001  85.830002  82.400024  1748400   
2019-01-02  84.029999  86.430000  83.959999  85.919998  82.486420  2523900   
2019-01-03  82.989998  84.349998  80.550003  80.730003  77.503830  4376600   
2019-01-04  81.459999  83.010002  80.459999  82.690002  79.385506  3470000   
2019-01-07  82.540001  84.190002  82.080002  83.209999  79.884720  2656300   

            Highest81  
Date                   
2018-12-31        NaN  
2019-01-02        NaN  
2019-01-03        NaN  
2019-01-04        NaN  
2019-01-07        NaN  
2019-02-27 00:00:00
2019-02-28 00:00:00
2019-03-05 00:00:00
2019-03-06 00:00:00
2019-03-07 00:00:00
2019-03-08 00:00:00
2019-03-11 00:00:00
2019-03-12 00:00:00
2019-03-13 00:00:00
2019-03-14 00:00:00
2019-03-15 0

KeyboardInterrupt: 